# Evolució socis i contractes de la Garrotxa - Python

In [96]:
import pandas as pd
import datetime

El grup local de la Garrotxa ens demana saber quina evolució han tingut per veure si les activitats de sensibilització que han fet el darrer any han tingut el seu efecte. L’Equip de Cultura Energètica ha rebut aquesta inquietud i li demana a l'Equip d'IT que munti un petit script per mostrar aquesta evolució i detectar els punts en la història amb major i menor creixement.

## Inspecció de les dades

Extreurem les dades necessàries del portal d'[Open Data](https://opendata.somenergia.coop/ui/) de Som Energia.

### Àmbit territorial

Llegint la [documentació](https://opendata.somenergia.coop/docs) de l'API del portal d'[Open Data](https://opendata.somenergia.coop/ui/) veiem que en principi existeix la unitat territorial 'localgroup'. Si bé al portal UI està deshabilitada sí que apareix a la documentació. Amb la crida /discover/geolevel/localgroup descobrim però que no hi ha l'entitat 'Garrotxa'. D'aquesta manra utilitzarem l'àmbit territorial municipal per obtenir les dades. Ens cal doncs, primer de tot, saber quins municipis conformen tota la Garrotxa. A l'[IDESCAT mateix](https://www.idescat.cat/codis/?id=50&n=10&c=19) podem trobar-los amb el codi corresponent, el mateix que fa servir la API de Som Energia.

### Selecció de les mètriques

Amb la crida /discover/metrics podem veure totes les mètriques disponibles. De moment farem servir socis i contractes (members, newmembers, canceledmembers, contracts, newcontracts, canceledcontracts. El grup local de la Garrotxa vol l'evolució de l'últim any però nosaltres hi inclourem el 2019 perquè el 2020 ha estat un any molt poc representatiu per la pandèmia i segurament això ha tingut un impacte en les dades que ens demanen.

Identificarem el procés d'importació i transformació necessari per a deixar les dades tal com les necessitem.

## Importem les dades

Confeccionem el link de la crida HTTP seguint les indicacions de la documentació indicant la mètrica que volem i tots els municipis de la Garrotxa.
Importem cada mètric per serparat amb la URL generada i ho adjuntem tot en un sol dataset.

In [97]:
# descarreguem les dades
url = 'https://opendata.somenergia.coop/v0.2/members/by/city/monthly/from/2019-01-01/to/2021-08-01?city=17010&city=17019&city=17021&city=17046&city=17098&city=17105&city=17109&city=17114&city=17133&city=17139&city=17149&city=17154&city=17183&city=17161&city=17162&city=17165&city=17185&city=17184&city=17200&city=17207&city=17208&format=tsv'
members = pd.read_csv(url, sep='\t').assign(metric = 'members')

url = 'https://opendata.somenergia.coop/v0.2/newmembers/by/city/monthly/from/2019-01-01/to/2021-08-01?city=17010&city=17019&city=17021&city=17046&city=17098&city=17105&city=17109&city=17114&city=17133&city=17139&city=17149&city=17154&city=17183&city=17161&city=17162&city=17165&city=17185&city=17184&city=17200&city=17207&city=17208&format=tsv'
newmembers = pd.read_csv(url, sep='\t').assign(metric = 'newmembers')

url = 'https://opendata.somenergia.coop/v0.2/canceledmembers/by/city/monthly/from/2019-01-01/to/2021-08-01?city=17010&city=17019&city=17021&city=17046&city=17098&city=17105&city=17109&city=17114&city=17133&city=17139&city=17149&city=17154&city=17183&city=17161&city=17162&city=17165&city=17185&city=17184&city=17200&city=17207&city=17208&format=tsv'
canceledmembers = pd.read_csv(url, sep='\t').assign(metric = 'canceledmembers')

url = 'https://opendata.somenergia.coop/v0.2/contracts/by/city/monthly/from/2019-01-01/to/2021-08-01?city=17010&city=17019&city=17021&city=17046&city=17098&city=17105&city=17109&city=17114&city=17133&city=17139&city=17149&city=17154&city=17183&city=17161&city=17162&city=17165&city=17185&city=17184&city=17200&city=17207&city=17208&format=tsv'
contracts = pd.read_csv(url, sep='\t').assign(metric = 'contracts')

url = 'https://opendata.somenergia.coop/v0.2/newcontracts/by/city/monthly/from/2019-01-01/to/2021-08-01?city=17010&city=17019&city=17021&city=17046&city=17098&city=17105&city=17109&city=17114&city=17133&city=17139&city=17149&city=17154&city=17183&city=17161&city=17162&city=17165&city=17185&city=17184&city=17200&city=17207&city=17208&format=tsv'
newcontracts = pd.read_csv(url, sep='\t').assign(metric = 'newcontracts')

url = 'https://opendata.somenergia.coop/v0.2/canceledcontracts/by/city/monthly/from/2019-01-01/to/2021-08-01?city=17010&city=17019&city=17021&city=17046&city=17098&city=17105&city=17109&city=17114&city=17133&city=17139&city=17149&city=17154&city=17183&city=17161&city=17162&city=17165&city=17185&city=17184&city=17200&city=17207&city=17208&format=tsv'
canceledcontracts = pd.read_csv(url, sep='\t').assign(metric = 'canceledcontracts')

# Ajuntem en un sol dataset
garrotxa = members.append(
    newmembers,
    ignore_index=True
).append(
    canceledmembers,
    ignore_index=True
).append(
    contracts,
    ignore_index=True
).append(
    newcontracts,
    ignore_index=True
).append(
    canceledcontracts,
    ignore_index=True
)

# COrregim posició de les columnes
first_column = garrotxa.pop('metric')
garrotxa.insert(0, 'metric', first_column)
garrotxa


metric country_code country  ccaa_code      ccaa  state_code  \
0              members           ES  España          9  Cataluña          17   
1              members           ES  España          9  Cataluña          17   
2              members           ES  España          9  Cataluña          17   
3              members           ES  España          9  Cataluña          17   
4              members           ES  España          9  Cataluña          17   
..                 ...          ...     ...        ...       ...         ...   
121  canceledcontracts           ES  España          9  Cataluña          17   
122  canceledcontracts           ES  España          9  Cataluña          17   
123  canceledcontracts           ES  España          9  Cataluña          17   
124  canceledcontracts           ES  España          9  Cataluña          17   
125  canceledcontracts           ES  España          9  Cataluña          17   

      state  city_code                      city  2019-01-01  ...  2020-11-01  \
0    Girona      17010                Argelaguer           8  ...          10   
1    Girona      17019                    Besalú          10  ...          11   
2    Girona      17021                     Beuda           4  ...           4   
3    Girona      17046  Castellfollit de la Roca           0  ...           1   
4    Girona      17098           Maià de Montcal           3  ...           3   
..      ...        ...                       ...         ...  ...         ...   
121  Girona      17165     Sant Jaume de Llierca           0  ...           0   
122  Girona      17185       Sant Joan les Fonts           0  ...           0   
123  Girona      17200                  Tortellà           0  ...           0   
124  Girona      17208        Vall de Bianya, La           0  ...           0   
125  Girona      17207         Vall d'en Bas, La           0  ...           0   

     2020-12-01  2021-01-01  2021-02-01  2021-03-01  2021-04-01  2021-05-01  \
0            10          10          10          10          10          10   
1            11          11          11          12          12          12   
2             4           4           4           4           4           4   
3             1           1           1           1           1           2   
4             4           5           5           6           6           6   
..          ...         ...         ...         ...         ...         ...   
121           0           0           0           0           0           0   
122           0           0           0           0           1           1   
123           0           0           0           0           0           0   
124           0           0           0           0           0           0   
125           2           1           1           0           0           0   

     2021-06-01  2021-07-01  2021-08-01  
0            10          10          10  
1            13          13          13  
2             4           4           4  
3             2           2           2  
4             6           6           6  
..          ...         ...         ...  
121           0           1           0  
122           0           0           0  
123           0           1           0  
124           0           0           0  
125           0           0           1  

[126 rows x 41 columns]

## Transformem les dades

Necessitem fer dos grans canvis: passar a dades llargues i agregar per comarca. Així, transformem les columnes que porten per nom la data a només dues columnes; una amb la data i l'altra amb el valor. Un cop fet això agregguem sumant els valors per comarca, data i tipus de mètrica.

In [98]:
garrotxa = garrotxa.melt(list(garrotxa.columns.values[0:9]), value_name = 'valor', var_name = 'mes')
garrotxa = garrotxa.assign(
    comarca = 'Garrotxa'
).assign(
    mes =  pd.to_datetime(garrotxa['mes'], format='%Y-%m-%d')
)
garrotxamunis = garrotxa # reservem pel mapa
garrotxa = garrotxa.groupby(['comarca', 'mes','metric'])['valor'].agg('sum').reset_index()
garrotxa

comarca        mes             metric  valor
0    Garrotxa 2019-01-01  canceledcontracts      1
1    Garrotxa 2019-01-01    canceledmembers      0
2    Garrotxa 2019-01-01          contracts    375
3    Garrotxa 2019-01-01            members    264
4    Garrotxa 2019-01-01       newcontracts      9
..        ...        ...                ...    ...
187  Garrotxa 2021-08-01    canceledmembers      0
188  Garrotxa 2021-08-01          contracts    640
189  Garrotxa 2021-08-01            members    411
190  Garrotxa 2021-08-01       newcontracts      3
191  Garrotxa 2021-08-01         newmembers      0

[192 rows x 4 columns]

## Visió general

Fem un graficat senzill de totes les mètriques per tenir una idea general.

In [99]:
import plotly.express as px
import plotly.offline as py

py.offline.init_notebook_mode(connected=True)

df = px.data.iris()

fig = px.bar(garrotxa, x="mes", y="valor", facet_col="metric")
fig.update_xaxes(title_font=dict(size=18, family='Courier', color='crimson'))
fig.update_yaxes(title_font=dict(size=18, family='Courier', color='crimson'))
fig.update_yaxes(matches=None, showticklabels=True)

fig.show()


Veiem per socis i contractes que hi ha una tendència general molt positiiva els últims dos anys amb un creixement mínim d'un 50%. També veiem l'impacte de la pandèmmia que atura els nous contractes i socis entre 2020 i principis del 2021. És un any atípic per treure conclusions d'actes de difusió potser.

## Impacte de les activitats

Per intentar avaluar l'impacte de les activitats organitzades pel grup local ens focalitzarem en les mètriques de noves altes en socis i contractes. Alternativament també podem fixar-nos en altes menys cancel·lacions per mirar d'avaluar un possible efecte negatiu de les activitats, si bé ja veiem que no semblen gaire significatives.


In [100]:
news = garrotxa[(garrotxa['metric'] == 'newcontracts') | (garrotxa['metric'] == 'newmembers')]

fig = px.line(news, x="mes", y="valor", facet_col="metric", facet_col_wrap=2)
fig.add_hline(y=news[news['metric'] == 'newmembers']['valor'].mean(), line_dash="dot",
              annotation_text="Mitjana nous membres",
              annotation_position="bottom right", col=2)
fig.add_vrect(x0="2020-03-01", x1="2020-06-30", col=2,
              annotation_text="confinament", annotation_position="top left",
              fillcolor="green", opacity=0.25, line_width=0)
fig.add_hline(y=news[news['metric'] == 'newcontracts']['valor'].mean(), line_dash="dot",
              annotation_text="Mitjana nous contractes",
              annotation_position="bottom right", col=1)
fig.add_vrect(x0="2020-03-01", x1="2020-06-30", col=1,
              annotation_text="confinament", annotation_position="top left",
              fillcolor="green", opacity=0.25, line_width=0)
fig.show()

Caldria tenir el calendari d'activitats del grup local i més informació sobre l'estacionalitat de les dades però veiem uns pics important el febrer, abril i agost-setembre de 2019, febrer-març del 2020 i febrer una altra vegada de 2021. Les dades d'agost 2021 i potser un o dos mesos abans no són representatives perquè encara no ha acabat el mes i el procés de contractació pot tardar.

### Mapa de creixement

Ja que tenim les dades per municipis podem fer un mapa per veure a quins punicipis ha crescut més Som Energia des de l'inici del període. No ponderarem per població, encara que no es pot comparar Olot amb la resta de municipis el % en pobles petits en comportaria de manera estranya.

Per fer-ho sumarem els nous socis i els nous contractes (per separat) de tots els mesos per cada municipi i ho representarem amb un mapa.

In [106]:
garrotxamunis = garrotxamunis.groupby(['city_code','metric', 'city'])['valor'].agg('sum').reset_index()
newsmunis = garrotxamunis[(garrotxamunis['metric'] == 'newcontracts') | (garrotxamunis['metric'] == 'newmembers')]

from urllib.request import urlopen
import json

with open('municipis_garrotxa.geojson') as fp:
    geojson = json.load(fp)
    
fig = px.choropleth(newsmunis, geojson=geojson, color="valor", facet_col="metric",
                    locations="city_code", featureidkey="properties.codiine",
                    projection="mercator", hover_data=["city"]
                   )
fig.update_geos(fitbounds="locations", visible=False)
fig.show()